In [1]:
import modeller
import fitter

import casadi as ca
from scipy.integrate import solve_ivp
import numpy as np
from matplotlib import pyplot as plt

In [2]:
p_true = [0.0005, 0.1]
tspan = [0, 20]
def system(t, y, p):
    return [
        -p[0]*y[0]*y[1],
        p[0]*y[0]*y[1] - p[1]*y[1],
        p[1]*y[1]
    ]
sol = solve_ivp(lambda t, y: system(t, y, p_true), tspan, [9999, 1, 0])

In [3]:
data = sol.y[-1, :]
data_pd = np.array([[i] for i in data])
config = {
    "grid_size": 100,
    "basis_number": 100,
    "model_form": {
        "state": 3,
        "parameters": 2
    },
    "time_span": tspan,
    "knot_function": None,
    "model": system,
    "dataset": {"y": data_pd, "t": sol.t},
    "observation_vector": [2],
    "weightings":[
        [1]*3,
        [1]*len(sol.t)
    ],
    "regularisation_value": p_true,
}

In [ ]:
model = modeller.Model(config)
objective = fitter.Objective()
objective.make(config, config['dataset'], model)

solver_setup = {
    'f': objective.objective,
    'x': ca.vcat(objective.input_list),
    'p': ca.hcat([objective.rho, objective.alpha])
}

solver = ca.nlpsol('solver', 'ipopt', solver_setup)

In [ ]:
p0 = 0.001*np.ones(2)
c0 = [c*np.ones(config['basis_number']) for c in [10000, 1, 0]]
x0 = np.hstack([*c0, p0])

In [ ]:
prange = np.logspace(-6, 6, num=200)
solutions = []
xguess = x0
for p in prange:
    solutions.append(solver(x0=xguess, p=[p, 1e-4], lbx=0))
    xguess = np.array(solutions[-1]['x']).flatten()


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************

This is Ipopt version 3.12.3, running with linear solver mumps.
NOTE: Other linear solvers might be more efficient (see Ipopt documentation).

Number of nonzeros in equality constraint Jacobian...:        0
Number of nonzeros in inequality constraint Jacobian.:        0
Number of nonzeros in Lagrangian Hessian.............:    35653

Total number of variables............................:      302
                     variables with only lower bounds:      302
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equa

  77 5.9145667e-002 0.00e+000 2.04e+004  -5.7 5.51e+004    -  6.98e-001 2.50e-001f  3
  78 5.9153181e-002 0.00e+000 1.23e+004  -5.7 7.50e+004 -13.2 6.68e-001 3.37e-004f 11
  79 5.8394363e-002 0.00e+000 5.68e+003  -5.7 4.70e+003    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
  80 5.7926469e-002 0.00e+000 1.08e+004  -5.7 1.84e+004    -  1.00e+000 5.00e-001f  2
  81 5.7389889e-002 0.00e+000 3.60e+003  -5.7 1.29e+004    -  1.00e+000 1.00e+000f  1
  82 5.7032368e-002 0.00e+000 5.58e+003  -5.7 5.54e+003    -  1.00e+000 1.00e+000f  1
  83 5.6809022e-002 0.00e+000 8.23e+002  -5.7 8.46e+003    -  1.00e+000 1.00e+000f  1
  84 5.6712465e-002 0.00e+000 9.65e+002  -5.7 1.97e+003    -  1.00e+000 1.00e+000f  1
  85 5.6691167e-002 0.00e+000 2.54e-001  -5.7 2.29e+002    -  1.00e+000 1.00e+000f  1
  86 5.6681610e-002 0.00e+000 7.30e+001  -5.7 2.26e+003    -  1.00e+000 1.00e+000f  1
  87 5.6676285e-002 0.00e+000 1.92e+001  -5.7 1.70e+002    

 169 3.2465479e-003 0.00e+000 8.14e+000  -8.6 2.65e+004    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 170 3.2460515e-003 0.00e+000 5.71e-001  -8.6 6.14e+003    -  1.00e+000 1.00e+000f  1
 171 3.2462693e-003 0.00e+000 7.40e+000  -8.6 9.69e+004    -  1.00e+000 2.50e-001f  3
 172 3.2458198e-003 0.00e+000 5.93e-001  -8.6 6.18e+003    -  1.00e+000 1.00e+000f  1
 173 3.2459313e-003 0.00e+000 5.98e+000  -8.6 8.46e+004    -  1.00e+000 2.50e-001f  3
 174 3.2455939e-003 0.00e+000 7.71e-001  -8.6 7.14e+003    -  1.00e+000 1.00e+000f  1
 175 3.2455606e-003 0.00e+000 3.35e+000  -8.6 5.86e+004    -  1.00e+000 2.50e-001f  3
 176 3.2453987e-003 0.00e+000 2.10e+000  -8.6 1.23e+004    -  1.00e+000 1.00e+000f  1
 177 3.2454159e-003 0.00e+000 4.96e+000  -8.6 1.91e+004    -  1.00e+000 1.00e+000f  1
 178 3.2451315e-003 0.00e+000 8.41e-001  -8.6 7.32e+003    -  1.00e+000 1.00e+000f  1
 179 3.2450759e-003 0.00e+000 2.38e+000  -8.6 4.47e+004    

   1 2.6093752e-001 0.00e+000 1.16e+004  -1.0 1.05e+002   0.0 1.58e-002 1.95e-001f  1
   2 6.9388281e-002 0.00e+000 1.07e+002  -1.0 1.00e+001    -  9.90e-001 1.00e+000f  1
   3 1.9812648e+000 0.00e+000 2.78e+003  -1.0 6.14e+002    -  9.56e-001 1.00e+000f  1
   4 1.9431177e+000 0.00e+000 4.70e+004  -1.0 4.13e+003    -  6.15e-001 3.41e-001f  1
   5 1.8557572e+000 0.00e+000 1.58e+005  -1.0 2.11e+003    -  4.10e-002 5.00e-001f  2
   6 1.0790459e+000 0.00e+000 5.41e+001  -1.0 6.82e-001  -0.5 9.92e-001 1.00e+000f  1
   7 1.1081139e+000 0.00e+000 1.43e+004  -1.0 1.02e+005    -  5.01e-001 4.96e-001f  1
   8 5.1268101e+000 0.00e+000 4.10e+005  -1.0 8.67e+004    -  7.96e-002 1.00e+000f  1
   9 9.9927477e-001 0.00e+000 6.15e-001  -1.0 9.80e-001  -1.0 1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
  10 2.2417046e-001 0.00e+000 5.04e+003  -1.7 9.64e+003    -  8.91e-001 1.00e+000f  1
  11 6.7836924e-001 0.00e+000 3.03e+005  -1.7 1.53e+004    

  93 6.4895722e-002 0.00e+000 4.88e+004  -8.6 3.54e+006    -  5.52e-001 1.25e-001f  4
  94 6.4723213e-002 0.00e+000 3.08e+004  -8.6 2.16e+003 -15.9 1.00e+000 1.00e+000f  1
  95 6.4625624e-002 0.00e+000 3.99e+004  -8.6 1.28e+006    -  1.00e+000 2.50e-001f  3
  96 6.4521269e-002 0.00e+000 3.89e+005  -8.6 1.35e+004 -16.4 1.00e+000 1.00e+000f  1
  97 6.4090411e-002 0.00e+000 5.78e+004  -8.6 3.24e+005    -  1.00e+000 1.00e+000f  1
  98 6.3890682e-002 0.00e+000 1.37e+005  -8.6 3.19e+005 -16.8 1.00e+000 1.25e-001f  4
  99 6.3531374e-002 0.00e+000 1.34e+005  -8.6 5.09e+005    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 100 6.2595130e-002 0.00e+000 1.13e+003  -8.6 3.07e+005    -  1.00e+000 1.00e+000f  1
 101 6.2093574e-002 0.00e+000 1.80e+005  -8.6 5.37e+004 -17.3 7.72e-001 8.99e-002f  4
 102 6.1233528e-002 0.00e+000 1.97e+005  -8.6 8.25e+005    -  1.00e+000 5.00e-001f  2
 103 5.9628834e-002 0.00e+000 2.63e+005  -8.6 6.90e+005    

...

 419 1.0915326e-001 0.00e+000 3.94e+002  -5.7 4.90e+003    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 420 1.0910638e-001 0.00e+000 2.24e+003  -5.7 4.22e+004    -  1.00e+000 2.50e-001f  3
 421 1.0904661e-001 0.00e+000 1.12e+003  -5.7 8.18e+003    -  1.00e+000 1.00e+000f  1
 422 1.0901013e-001 0.00e+000 4.26e+003  -5.7 1.58e+004    -  1.00e+000 1.00e+000f  1
 423 1.0892878e-001 0.00e+000 2.89e+002  -5.7 4.25e+003    -  1.00e+000 1.00e+000f  1
 424 1.0888823e-001 0.00e+000 3.31e+003  -5.7 5.38e+004    -  1.00e+000 2.50e-001f  3
 425 1.0882559e-001 0.00e+000 4.62e+002  -5.7 5.37e+003    -  1.00e+000 1.00e+000f  1
 426 1.0878618e-001 0.00e+000 1.62e+003  -5.7 3.49e+004    -  1.00e+000 2.50e-001f  3
 427 1.0873257e-001 0.00e+000 1.84e+003  -5.7 1.06e+004    -  1.00e+000 1.00e+000f  1
 428 1.0868013e-001 0.00e+000 1.40e+003  -5.7 9.28e+003    -  1.00e+000 1.00e+000f  1
 429 1.0862957e-001 0.00e+000 2.34e+003  -5.7 1.20e+004    

 509 1.0658911e-001 0.00e+000 4.87e+002  -5.7 1.14e+004    -  1.00e+000 5.00e-001f  2
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 510 1.0658056e-001 0.00e+000 2.18e+002  -5.7 4.23e+003    -  1.00e+000 1.00e+000f  1
 511 1.0656570e-001 0.00e+000 8.35e+002  -5.7 8.26e+003    -  1.00e+000 1.00e+000f  1
 512 1.0656052e-001 0.00e+000 5.28e+001  -5.7 2.11e+003    -  1.00e+000 1.00e+000f  1
 513 1.0655089e-001 0.00e+000 3.64e+002  -5.7 2.06e+004    -  1.00e+000 2.50e-001f  3
 514 1.0654308e-001 0.00e+000 1.97e+002  -5.7 4.04e+003    -  1.00e+000 1.00e+000f  1
 515 1.0653129e-001 0.00e+000 5.05e+002  -5.7 6.45e+003    -  1.00e+000 1.00e+000f  1
 516 1.0652641e-001 0.00e+000 6.84e+001  -5.7 2.39e+003    -  1.00e+000 1.00e+000f  1
 517 1.0651551e-001 0.00e+000 4.77e+002  -5.7 1.21e+004    -  1.00e+000 5.00e-001f  2
 518 1.0651142e-001 0.00e+000 4.83e+001  -5.7 2.02e+003    -  1.00e+000 1.00e+000f  1
 519 1.0650074e-001 0.00e+000 4.55e+002  -5.7 1.20e+004    

 599 1.0552631e-001 0.00e+000 8.59e+002  -8.6 9.88e+003    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 600 1.0551983e-001 0.00e+000 1.72e+003  -8.6 2.41e+004    -  1.00e+000 5.00e-001f  2
 601 1.0551008e-001 0.00e+000 1.31e+003  -8.6 1.22e+004    -  1.00e+000 1.00e+000f  1
 602 1.0550210e-001 0.00e+000 2.24e+003  -8.6 1.59e+004    -  1.00e+000 1.00e+000f  1
 603 1.0549161e-001 0.00e+000 7.58e+002  -8.6 9.35e+003    -  1.00e+000 1.00e+000f  1
 604 1.0548554e-001 0.00e+000 1.98e+003  -8.6 2.70e+004    -  1.00e+000 5.00e-001f  2
 605 1.0547578e-001 0.00e+000 9.56e+002  -8.6 1.05e+004    -  1.00e+000 1.00e+000f  1
 606 1.0547532e-001 0.00e+000 4.01e+003  -8.6 2.14e+004    -  1.00e+000 1.00e+000f  1
 607 1.0545755e-001 0.00e+000 2.26e+002  -8.6 5.22e+003    -  1.00e+000 1.00e+000f  1
 608 1.0545194e-001 0.00e+000 1.16e+003  -8.6 8.42e+004    -  1.00e+000 1.25e-001f  4
 609 1.0544589e-001 0.00e+000 2.68e+003  -8.6 1.77e+004    

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 690 1.0503334e-001 0.00e+000 8.36e+002  -8.6 1.12e+004    -  1.00e+000 1.00e+000f  1
 691 1.0503185e-001 0.00e+000 2.63e+003  -8.6 1.99e+004    -  1.00e+000 1.00e+000f  1
 692 1.0502673e-001 0.00e+000 2.64e+002  -8.6 6.39e+003    -  1.00e+000 1.00e+000f  1
 693 1.0502466e-001 0.00e+000 1.68e+003  -8.6 5.98e+004    -  1.00e+000 2.50e-001f  3
 694 1.0502110e-001 0.00e+000 6.38e+002  -8.6 9.90e+003    -  1.00e+000 1.00e+000f  1
 695 1.0501896e-001 0.00e+000 1.39e+003  -8.6 2.54e+004    -  1.00e+000 5.00e-001f  2
 696 1.0501570e-001 0.00e+000 9.24e+002  -8.6 1.19e+004    -  1.00e+000 1.00e+000f  1
 697 1.0501343e-001 0.00e+000 2.05e+003  -8.6 1.77e+004    -  1.00e+000 1.00e+000f  1
 698 1.0500959e-001 0.00e+000 4.17e+002  -8.6 8.05e+003    -  1.00e+000 1.00e+000f  1
 699 1.0500872e-001 0.00e+000 2.60e+003  -8.6 3.83e+004    -  1.00e+000 5.00e-001f  2
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) 

 777 1.0486024e-001 0.00e+000 1.82e+002  -8.6 5.93e+003    -  1.00e+000 1.00e+000f  1
 778 1.0485952e-001 0.00e+000 1.58e+003  -8.6 6.54e+004    -  1.00e+000 2.50e-001f  3
 779 1.0485795e-001 0.00e+000 3.32e+002  -8.6 7.95e+003    -  1.00e+000 1.00e+000f  1
iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alpha_pr  ls
 780 1.0485745e-001 0.00e+000 1.90e+003  -8.6 3.60e+004    -  1.00e+000 5.00e-001f  2
 781 1.0485562e-001 0.00e+000 2.24e+002  -8.6 6.56e+003    -  1.00e+000 1.00e+000f  1
 782 1.0485479e-001 0.00e+000 1.05e+003  -8.6 5.14e+004    -  1.00e+000 2.50e-001f  3
 783 1.0485353e-001 0.00e+000 7.13e+002  -8.6 1.16e+004    -  1.00e+000 1.00e+000f  1
 784 1.0485262e-001 0.00e+000 1.56e+003  -8.6 1.72e+004    -  1.00e+000 1.00e+000f  1
 785 1.0485113e-001 0.00e+000 3.24e+002  -8.6 7.87e+003    -  1.00e+000 1.00e+000f  1
 786 1.0485070e-001 0.00e+000 1.90e+003  -8.6 3.62e+004    -  1.00e+000 5.00e-001f  2
 787 1.0484895e-001 0.00e+000 2.12e+002  -8.6 6.42e+003    

In [ ]:
f1_ex = ca.Function('f1_ex', [solver_setup['x']], [objective.obj_1])
f2_ex = ca.Function('f2_ex', [solver_setup['x']], [objective.obj_2])

In [ ]:
fsvals = np.array([(float(f1_ex(s['x'])), float(f2_ex(s['x']))) for s in solutions])

In [ ]:
plt.loglog(*fsvals.T)

In [ ]:
plt.loglog(prange, [float(s['x'][0]) for s in solutions])
plt.loglog(prange, [float(s['x'][1]) for s in solutions])

In [ ]:
getx = ca.Function('getx', [solver_setup['x']], model.xs)
getp = ca.Function('getp', [solver_setup['x']], model.ps)

In [ ]:
print([float(p) for p in getp(solutions[-1]['x'])])
plt.plot(model.observation_times, getx(solutions[-1]['x'])[-1], label='model')
plt.plot(sol.t, sol.y[-1,:], 'o', label='data')

In [ ]:
xs_recovered = getx(solutions[-1]['x'])
[float(x[10]) for x in xs_recovered]

In [ ]:
p_recovered = solutions[-1]['x'][:2]
sol_recovered = solve_ivp(lambda t, y: system(t, y, p_recovered), tspan, [x[0] for x in xs_recovered])
plt.plot(sol_recovered.t, sol_recovered.y.T)